In [8]:
import sys
sys.path.append('../utils')
# from torch_trajectory import slerp_batch
import trimesh 
import torch
import roma
from scipy.spatial.transform import Rotation as R   
import numpy as np

device = 'cpu'

In [9]:
rot = roma.random_rotvec(1000).to(device)

In [10]:
# init_quat = torch.tensor([0, -0.707, -0.707, 0.0]).reshape(-1, 4).to(device)
# goal_quat = torch.tensor([0, 0, 0.707, 0.707]).reshape(-1, 4).to(device)
steps = torch.linspace(0, 1, 100).to(device)

init_quat = roma.rotvec_to_unitquat(rot)
goal_quat = roma.random_unitquat(1000).to(device)

In [12]:
slerp_quats = roma.unitquat_slerp(init_quat, goal_quat, steps=steps)
slerp_quats.shape

torch.Size([100, 1000, 4])

In [68]:
frame = trimesh.creation.axis(origin_size=0.1)
frames = []
for i, t in enumerate(range(100)):
    rot = roma.unitquat_to_rotmat(slerp_quats[i]).cpu().numpy()
    rot_map = np.eye(4)
    rot_map[:3, :3] = rot
    frame_rot = frame.copy()
    frame_rot.apply_transform(rot_map)
    frame_rot.apply_translation([0, 0.1 * i, 0.2 * i])
    frames.append(frame_rot)
    

In [69]:
scene = trimesh.Scene([*frames, trimesh.creation.axis(origin_size=0.5)])
scene.show()

In [13]:
import torch

def compute_quintic_coefficients(start, goal, start_vel, goal_vel, start_acc, goal_acc, duration):
    """
    Compute coefficients of the quintic polynomial for 1D motion.
    
    Parameters:
        start (float or Tensor): Start position.
        goal (float or Tensor): Goal position.
        start_vel (float or Tensor): Start velocity.
        goal_vel (float or Tensor): Goal velocity.
        start_acc (float or Tensor): Start acceleration.
        goal_acc (float or Tensor): Goal acceleration.
        duration (float or Tensor): Total time to reach goal.
    
    Returns:
        Tensor: Coefficients [a0, a1, a2, a3, a4, a5] of the quintic polynomial.
    """
    t0 = 0
    tf = duration

    # Construct the matrix for solving coefficients
    A = torch.tensor([
        [1, t0, t0**2, t0**3, t0**4, t0**5],
        [0, 1, 2*t0, 3*t0**2, 4*t0**3, 5*t0**4],
        [0, 0, 2, 6*t0, 12*t0**2, 20*t0**3],
        [1, tf, tf**2, tf**3, tf**4, tf**5],
        [0, 1, 2*tf, 3*tf**2, 4*tf**3, 5*tf**4],
        [0, 0, 2, 6*tf, 12*tf**2, 20*tf**3]
    ], dtype=start.dtype)

    b = torch.stack([
        start, start_vel, start_acc,
        goal, goal_vel, goal_acc
    ], dim=-1)

    # Solve for coefficients
    coeffs = torch.linalg.solve(A, b)
    return coeffs


def compute_trajectory(coeffs, t):
    """
    Compute the trajectory at time t using quintic polynomial coefficients.
    
    Parameters:
        coeffs (Tensor): Coefficiets [a0, a1, a2, a3, a4, a5] of shape (N, 6).
        t (Tensor): Time points of shape (T,).
    
    Returns:
        Tensor: Trajectory positions of shape (N, T).
    """
    t_vec = torch.stack([t**i for i in range(6)], dim=-1)  # (T, 6)
    return torch.matmul(t_vec, coeffs.T)  # (T, N) -> Transpose to get (N, T)


def generate_3d_trajectory(start_pos, goal_pos, duration, timesteps):
    """
    Generate a 3D trajectory using quintic polynomials for x, y, z components.

    Parameters:
        start_pos (Tensor): Start positions of shape (N, 3).
        goal_pos (Tensor): Goal positions of shape (N, 3).
        duration (float): Duration to reach the goal.
        timesteps (int): Number of timesteps in the trajectory.
    
    Returns:
        Tensor: 3D trajectory of shape (N, timesteps, 3).
    """
    t = torch.linspace(0, duration, timesteps)  # Time points
    N = start_pos.shape[0]
    trajectory = torch.zeros(N, timesteps, 3, dtype=start_pos.dtype)

    for dim in range(3):  # Compute for x, y, z separately
        coeffs = compute_quintic_coefficients(
            start=start_pos[:, dim],
            goal=goal_pos[:, dim],
            start_vel=torch.zeros(N, dtype=start_pos.dtype),
            goal_vel=torch.zeros(N, dtype=start_pos.dtype),
            start_acc=torch.zeros(N, dtype=start_pos.dtype),
            goal_acc=torch.zeros(N, dtype=start_pos.dtype),
            duration=duration
        )
        trajectory[:, :, dim] = compute_trajectory(coeffs, t)
    
    return trajectory



In [67]:

batch_size = 128
init_pos = torch.zeros(batch_size, 3)
init_vel = torch.zeros(batch_size)
init_accel = torch.zeros(batch_size)
final_pos = torch.randn(batch_size, 3) * 10

final_vel = torch.randn(batch_size)
final_accel = torch.randn(batch_size)
dist = torch.ones(batch_size) * 1.0

s = torch.linspace(0, 1, steps=1000)  # Time points

qp_x = QuinticPolynomial(init_pos[:, 0], init_vel, init_accel, final_pos[:, 0], final_vel, final_accel, dist)
qp_y = QuinticPolynomial(init_pos[:, 1], init_vel, init_accel, final_pos[:, 1], final_vel, final_accel, dist)
qp_z = QuinticPolynomial(init_pos[:, 2], init_vel, init_accel, final_pos[:, 2], final_vel, final_accel, dist)



In [68]:
traj = torch.stack([qp_x.calc_point(s), qp_y.calc_point(s), qp_z.calc_point(s)], dim=-1)
traj.shape

torch.Size([128, 1000, 3])

In [69]:
frame = trimesh.creation.axis(origin_size=0.1)
frames = []

for i in range(len(s)):
    frame_rot = frame.copy()
    frame_rot.apply_translation(traj[0][i].cpu().numpy())
    frames.append(frame_rot)
    
scene = trimesh.Scene([*frames, trimesh.creation.axis(origin_size=0.5)])
scene.show()

In [70]:
traj[0]

tensor([[ 0.0000e+00,  0.0000e+00,  0.0000e+00],
        [ 1.2286e-08, -2.4683e-07, -3.9975e-08],
        [ 9.8147e-08, -1.9717e-06, -3.1932e-07],
        ...,
        [ 1.3231e+00, -2.4550e+01, -3.8952e+00],
        [ 1.3231e+00, -2.4550e+01, -3.8952e+00],
        [ 1.3231e+00, -2.4550e+01, -3.8952e+00]])

In [71]:
final_pos[0]

tensor([  1.3231, -24.5500,  -3.8951])